In [1]:
# Verifying that we are using osx-arm64 arch
import platform
platform.platform(), platform.mac_ver()

('macOS-13.2.1-arm64-i386-64bit', ('13.2.1', ('', '', ''), 'arm64'))

In [2]:
import tensorflow as tf
tf.__version__

'2.9.0'

In [3]:
len(tf.config.list_physical_devices('GPU'))>0

True

In [4]:
tf.config.list_physical_devices('GPU')

[PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]

In [6]:
gpus = tf.config.list_physical_devices('GPU')
tf.config.set_visible_devices(gpus[0], 'GPU')

## BERT example

In [7]:
import tensorflow as tf
import transformers
import pandas as pd
import numpy as np

from transformers import BertTokenizer, TFBertForSequenceClassification
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_recall_fscore_support

/Users/mash/miniconda3/envs/tf/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [8]:
checkpoint = "bert-base-multilingual-cased"
tokenizer = BertTokenizer.from_pretrained(checkpoint)
model = TFBertForSequenceClassification.from_pretrained(checkpoint)

Metal device set to: Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Apple M1

systemMemory: 8.00 GB
maxCacheSize: 2.67 GB

Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Shape in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Fill in device /job:lo

2023-03-15 18:11:34.056873: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:305] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2023-03-15 18:11:34.057601: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:271] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)


Executing op Mul in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AddV2 in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op TruncatedNormal in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Mul in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AddV2 in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op TruncatedNormal in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Mul in device /job:localhost/replica:

All model checkpoint layers were used when initializing TFBertForSequenceClassification.

Some layers of TFBertForSequenceClassification were not initialized from the model checkpoint at bert-base-multilingual-cased and are newly initialized: ['classifier']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [9]:
# Data paths
data_training_en_path = '../Author profiling/Datasets/PAN19-Author-Profiling-20200229/CSV/Clean/data_training_en.csv'
data_training_es_path = '../Author profiling/Datasets/PAN19-Author-Profiling-20200229/CSV/Clean/data_training_es.csv'
data_test_en_path = '../Author profiling/Datasets/PAN19-Author-Profiling-20200229/CSV/Clean/data_test_en.csv'
data_test_es_path = '../Author profiling/Datasets/PAN19-Author-Profiling-20200229/CSV/Clean/data_test_es.csv'

In [10]:
# Data
data_training_en = pd.read_csv(data_training_en_path)
data_test_en = pd.read_csv(data_test_en_path)

data_training_es = pd.read_csv(data_training_es_path)
data_test_es = pd.read_csv(data_test_es_path)

In [11]:
data_training_en = data_training_en.dropna()
data_test_en = data_test_en.dropna()
data_training_es = data_training_es.dropna()
data_test_es = data_test_es.dropna()

In [12]:
# Cargar los datos de entrenamiento y prueba
train_data = pd.concat([data_training_en, data_training_es], axis=0)
test_data = pd.concat([data_test_en, data_test_es], axis=0)

In [13]:
train_data = train_data.drop(['Unnamed: 0.1', 'Unnamed: 0'], axis=1)
test_data = test_data.drop(['Unnamed: 0.1', 'Unnamed: 0'], axis=1)

In [14]:
train_data.head()

id  \
0  1008c35dc72c34ead679c539a0ed7c24   
1  1008c35dc72c34ead679c539a0ed7c24   
2  1008c35dc72c34ead679c539a0ed7c24   
3  1008c35dc72c34ead679c539a0ed7c24   
4  1008c35dc72c34ead679c539a0ed7c24   

                                               tweet  author  gender  
0            i can hear the black bull jukey calling       0       0  
1                            or the agincourt salute       0       0  
2  insight into how challenging touring is for a ...       0       0  
3     flight of the rat classic purps boogie on down       0       0  
4  he switched his twitter aff give him a poke on...       0       0

In [15]:
train_data.isna().sum()

id        0
tweet     0
author    0
gender    0
dtype: int64

In [16]:
train_data['text_length'] = train_data['tweet'].apply(len)
avg_text_length = train_data['text_length'].mean()
print(f'Longitud promedio de los textos del conjunto de entrenamiento: {round(avg_text_length, 1)}')

Longitud promedio de los textos del conjunto de entrenamiento: 77.0


In [17]:
train_encodings = tokenizer(train_data['tweet'].tolist(), 
                            truncation=True, 
                            padding=True, 
                            max_length=77)
train_dataset = tf.data.Dataset.from_tensor_slices((
    dict(train_encodings),
    train_data['author'].tolist()
)).shuffle(1000).batch(32)

Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op TensorSliceDataset in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op DummySeedGenerator in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op ShuffleDatasetV3 in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op BatchDatasetV2 in device /job:localhost/replica:0/task:0/device:CPU:0


In [18]:
test_encodings = tokenizer(test_data['tweet'].tolist(), 
                           truncation=True, 
                           padding=True, 
                           max_length=77)
test_dataset = tf.data.Dataset.from_tensor_slices((
    dict(test_encodings),
    test_data['author'].tolist()
)).batch(32)

Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op TensorSliceDataset in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op BatchDatasetV2 in device /job:localhost/replica:0/task:0/device:CPU:0


In [21]:
model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=2e-5, epsilon=1e-08, clipnorm=1.0),
              loss=model.hf_compute_loss, metrics=['accuracy'])

Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0


In [22]:
history = model.fit(train_dataset, validation_data=test_dataset, epochs=3)

Executing op DatasetCardinality in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op DatasetCardinality in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Equal in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op GreaterEqual in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Identity i

2023-03-15 18:13:42.494694: I tensorflow/core/common_runtime/placer.cc:114] iterator: (_Arg): /job:localhost/replica:0/task:0/device:CPU:0
2023-03-15 18:13:42.494951: I tensorflow/core/common_runtime/placer.cc:114] tf_bert_for_sequence_classification_bert_embeddings_gather_resource: (_Arg): /job:localhost/replica:0/task:0/device:GPU:0
2023-03-15 18:13:42.494957: I tensorflow/core/common_runtime/placer.cc:114] tf_bert_for_sequence_classification_bert_embeddings_gather_1_resource: (_Arg): /job:localhost/replica:0/task:0/device:GPU:0
2023-03-15 18:13:42.495009: I tensorflow/core/common_runtime/placer.cc:114] tf_bert_for_sequence_classification_bert_embeddings_gather_2_resource: (_Arg): /job:localhost/replica:0/task:0/device:GPU:0
2023-03-15 18:13:42.495014: I tensorflow/core/common_runtime/placer.cc:114] tf_bert_for_sequence_classification_bert_embeddings_layernorm_batchnorm_mul_readvariableop_resource: (_Arg): /job:localhost/replica:0/task:0/device:GPU:0
2023-03-15 18:13:42.495017: I ten

Executing op __inference_train_function_34517 in device /job:localhost/replica:0/task:0/device:GPU:0
   1/3741 [..............................] - ETA: 36:17:32 - loss: 0.7536 - accuracy: 0.3438Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op __inference_train_function_34517 in device /job:localhost/replica:0/task:0/device:GPU:0
   2/3741 [..............................] - ETA: 6:49:56 - loss: 0.7212 - accuracy: 0.4062 Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op __inference_train_function_34517 in device /job:localhost/replica:0/task:0/device:GPU:0
   3/3741 [..............................] - ETA: 9:01:31 - loss: 0.6946 - accuracy: 0.4688Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Identi

In [ ]:
# Evaluar el modelo
test_predictions = model.predict(test_dataset)
test_predictions = tf.nn.sigmoid(test_predictions.logits)
test_predictions = tf.round(test_predictions)
test_predictions = test_predictions.numpy().astype(int)
test_labels = test_data["label"].tolist()

accuracy = accuracy_score(test_labels, test_predictions)
precision, recall, f1_score, _ = precision_recall_fscore_support(test_labels, test_predictions, average="binary")

In [ ]:
print(f'precision: {precision}')
print(f'recall: {recall}')
print(f'f1: {f1}')